In [1]:
import sys
import os
import copy
import random
import gym
import pickle

import numpy as np
import pandas as pd
import tensorflow as tf
tf.keras.backend.set_floatx('float32')

from itertools import permutations
from sklearn.model_selection import KFold, GridSearchCV

from multiprocessing import set_start_method
import multiprocessing as mp

path = os.path.abspath('..')
if path not in sys.path:
    sys.path.append(path)

from seal.agents.default_config import DEFAULT_CONFIG as config
from seal.agents.dqn import DQNAgent
# from seal.agents.qr_dqn import QuantileAgent
# from seal.agents.multi_head_dqn import MultiHeadDQNAgent
# from seal.agents.discrete_bcq import DiscreteBCQAgent

from seal.algos.kfold import CVS, KFoldCV
from seal.algos.advantage_learner import AdvantageLearner
from seal.algos.behavior_cloning import BehaviorCloning
from seal.algos.density_ratio import VisitationRatioModel
from seal.algos.fqe import FQE

def one_step(seed):
    np.random.seed(seed)
    tf.random.set_seed(seed)
    
    path = './data/mh/dqn/trajs_mh.pkl'
    nfolds = 5
    n_splits = 5
    ckpts = (np.arange(20) + 1)*1000
    
    num_actions = 5
    # configures
    config['online'] = False
    config['lr'] = 5e-4
    config['decay_steps'] = 50000
    config['max_training_steps'] = 10000
    config['training_steps_to_checkpoint'] = 1000
    config['training_steps_to_eval'] = 100000
    config['hiddens'] = [64,64]
    config['double'] = False
    config['dueling'] = False

    index = pd.MultiIndex.from_product([np.arange(nfolds), ckpts])
    columns = ['dqn',  'seal']
    rets = pd.DataFrame(index=index, columns=columns)

    print('-'*20, 'start', '-'*20)
    cvs = CVS(path, n_splits=nfolds, random_state=seed)
    cvs.split()
    for fold in range(nfolds):
        train_path = cvs.train_paths[fold] + 'trajs.pkl'
        kf = KFoldCV(train_path, n_trajs=None, n_splits=n_splits, shuffle=False, random_state=seed)
        kf.split()

        print('-'*20, 'training agent', '-'*20)
        # agent
        config['persistent_directory'] = kf.agent_path
        config['checkpoint_path'] = kf.ckpt_path
        agent = DQNAgent(num_actions=num_actions, config=config)
        agent.learn()

        print('-'*20, 'training agents', '-'*20)
        # agent_1, ..., agent_K
        for idx in range(kf.n_splits):
            config_idx = copy.deepcopy(config)
            config_idx['persistent_directory'] = kf.agent_paths[idx]
            config_idx['checkpoint_path'] = kf.ckpt_paths[idx]
            agent_idx = DQNAgent(num_actions=num_actions, config=config_idx)
            agent_idx.learn()

        # fitted q evaluation
        test_path = cvs.test_paths[fold] + 'trajs.pkl'
        with open(test_path, 'rb') as f:
            trajs = pickle.load(f)

        print('-'*20, 'behavior cloning', '-'*20)
        # behavior cloning
        bc = BehaviorCloning(num_actions=num_actions)
        states  = np.array([transition[0] for traj in kf.trajs for transition in traj])
        actions = np.array([transition[1] for traj in kf.trajs for transition in traj])
        bc.train(states, actions)

        for ckpt in ckpts:
            print('-'*20, 'ckpt: ', ckpt, '-'*20)
            agent = DQNAgent(num_actions=num_actions, config=config)
            agent.load(kf.ckpt_path + 'offline_dqn_{}.ckpt'.format(ckpt))

            agents = []
            for idx in range(kf.n_splits):
                config_idx = copy.deepcopy(config)
                config_idx['persistent_directory'] = kf.agent_paths[idx]
                config_idx['checkpoint_path'] = kf.ckpt_paths[idx]
                agent_idx = DQNAgent(num_actions=num_actions, config=config_idx)
                agent_idx.load(kf.ckpt_paths[idx] + 'offline_dqn_{}.ckpt'.format(ckpt))
                agents.append(agent_idx)
            states, qvalues, qtildes = kf.update_q(agents, bc)

            print('-'*20, 'adv learner', '-'*20)
#             advs1 = qvalues - qvalues.mean(axis=1, keepdims=True)
#             agent1 = AdvantageLearner(num_actions=num_actions)
#             agent1._train(states, advs1)
            
            advs2 = qtildes - qtildes.mean(axis=1, keepdims=True)
            agent2 = AdvantageLearner(num_actions=num_actions)
            agent2._train(states, advs2)

            print('-'*20, 'fqe on dqn & seal', '-'*20)
            fqe_dqn = FQE(agent.greedy_actions, num_actions=num_actions, activation='tanh', hiddens=config['hiddens'], max_iter=100, eps=0.0015)
            fqe_dqn.train(trajs)
#             fqe_dml = FQE(agent1.greedy_actions, num_actions=num_actions)
#             fqe_dml.train(trajs)
            fqe_seal = FQE(agent2.greedy_actions, num_actions=num_actions, activation='tanh', hiddens=config['hiddens'], max_iter=100, eps=0.0015)
            fqe_seal.train(trajs)

            rets.loc[(fold, ckpt), 'dqn'] = fqe_dqn.values
#             rets.loc[(fold, ckpt), 'dml'] = fqe_dml.values
            rets.loc[(fold, ckpt), 'seal'] = fqe_seal.values
            
    return rets

In [2]:
save_path = './data/mh/dqn/'
pool = mp.Pool(5)
rets = pool.map(one_step, range(5))
pool.close()

with open(save_path + 'rets_dqn_mh.pkl', 'wb') as f:
    pickle.dump(rets, f)

----------------------------------------------------------------------------------------------------    start startstart startstart --------------------  --------------------
----------------------------------------
 

--------------------
-------------------- training agent --------------------
------------------------------------------------------------ --------------------  training agent training agenttraining agent training agent --------------------  --------------------
--------------------
--------------------

Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/209652396/fold0/train/agent/trajs.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/798842024/fold0/train/agent/trajs.pkl!Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold0/train/agent/trajs.pkl!

Refresh buffer every 1000000 sampling!Refresh buffer every 1000000 sampling!

Loaded tra


saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/717354021/fold0/train/agent/ckpt/offline_dqn_1000.ckptsaving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold0/train/agent/ckpt/offline_dqn_1000.ckpt

saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/218175338/fold0/train/agent/ckpt/offline_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/798842024/fold0/train/agent/ckpt/offline_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/209652396/fold0/train/agent/ckpt/offline_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/717354021/fold0/train/agent/ckpt/offline_dqn_2000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold0/train/agent/ckpt/offline_dqn_2000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/218175338/fold0/train/agent/ckpt/offline_dqn_2000.ckpt
saving model weights at /home/jupyt/ley


saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/209652396/fold0/train/agent/ckpt/offline_dqn_20000.ckpt
-------------------- training agents --------------------
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/209652396/fold0/train/agent0/trajs0.pkl!
Refresh buffer every 1000000 sampling!

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X mo

Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/717354021/fold0/train/agent1/trajs1.pkl!
Refresh buffer every 1000000 sampling!

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the l


saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold0/train/agent1/ckpt/offline_dqn_4000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/209652396/fold0/train/agent1/ckpt/offline_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/717354021/fold0/train/agent1/ckpt/offline_dqn_4000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/798842024/fold0/train/agent1/ckpt/offline_dqn_3000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/218175338/fold0/train/agent1/ckpt/offline_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold0/train/agent1/ckpt/offline_dqn_5000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/209652396/fold0/train/agent1/ckpt/offline_dqn_2000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/717354021/fold0/train/agent1/ckpt/offline_dqn_5000.ckpt
saving model weights at /home/j

...

Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold4/train/agent0/trajs0.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold4/train/agent1/trajs1.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold4/train/agent2/trajs2.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold4/train/agent3/trajs3.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/dqn/tmp/932136058/fold4/train/agent4/trajs4.pkl!
Refresh buffer every 1000000 sampling!

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers t


-----iteration:  0 target diff:  0.9179125048776294 values:  -47.368732 ----- 

-----iteration:  1 target diff:  0.0028891143596579552 values:  -47.36121 ----- 

-----iteration:  2 target diff:  0.0027007147073766606 values:  -47.38648 ----- 

-----iteration:  3 target diff:  0.002361533827989079 values:  -47.399715 ----- 

-----iteration:  4 target diff:  0.002110864486957571 values:  -47.451843 ----- 

-----iteration:  5 target diff:  0.0027119382608808847 values:  -47.473934 ----- 

-----iteration:  6 target diff:  0.0024925765723616882 values:  -47.4764 ----- 

-----iteration:  7 target diff:  0.001811156573431088 values:  -47.49527 ----- 

-----iteration:  8 target diff:  0.0023612386046100147 values:  -47.57231 ----- 

-----iteration:  9 target diff:  0.002910601115727355 values:  -47.551083 ----- 

-----iteration:  10 target diff:  0.0025125408388768384 values:  -47.592045 ----- 

-----iteration:  11 target diff:  0.0029357384514551274 values:  -47.58767 ----- 

-----iteration:



If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

---------------


-----iteration:  87 target diff:  0.0018303052776982947 values:  -42.355045 ----- 

-----iteration:  88 target diff:  0.0019437202592138638 values:  -42.3803 ----- 

-----iteration:  89 target diff:  0.002312372615165089 values:  -42.360687 ----- 

-----iteration:  90 target diff:  0.001989698781230027 values:  -42.373375 ----- 

-----iteration:  91 target diff:  0.0018306296591025565 values:  -42.384933 ----- 

-----iteration:  92 target diff:  0.0021153178674576086 values:  -42.355854 ----- 

-----iteration:  93 target diff:  0.0018339266193784201 values:  -42.377144 ----- 

-----iteration:  94 target diff:  0.002003365132809982 values:  -42.386887 ----- 

-----iteration:  95 target diff:  0.0019107880748988853 values:  -42.405037 ----- 

-----iteration:  96 target diff:  0.002059472393311861 values:  -42.44908 ----- 

-----iteration:  97 target diff:  0.00198331566451506 values:  -42.468117 ----- 

-----iteration:  98 target diff:  0.0020580966544573504 values:  -42.4839 ----- 

--



If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

---------------